In [1]:
cd ..

C:\Users\wpgur\OneDrive\프로그래밍\Back-End\tdatlib


In [2]:
from IPython.display import display, HTML
display(HTML("<style>.container { width:80% !important;}</style>"))

import plotly.graph_objects as go
import pandas as pd
import numpy as np
from plotly.subplots import make_subplots
from tqdm.notebook import tqdm
from snob import tools, ecos, fred, krse, idex, kr

# The Basics

(Thumbnail)

<b>요약</b>
* '80년대 John Bollinger에 의해 개발
* 중심선과 상/하 가격 밴드로 구성
* 중심선은 단순 이동 평균(SMA)으로 계산되며 상/하 밴드는 대상 증권의 표준 편차로 계산
* 밴드는 가격 변동이 클 때 팽창하고 작을 때 수축
* 상/하 밴드를 목표가로 트레이딩하기 위한 목적으로 개발

볼린저 밴드는 미국의 재무 분석가 존 볼린저(John A. Bollinger, 1950.5.27~)에 의해 개발된 유가 증권의 기술적 분석 도구입니다. 정의는 꽤 단순합니다. 주가의 이동평균선을 중심선으로 하고 가격의 변동성을 나타내는 이동표준편차를 상/하단에 일정 거리만큼 두어 위치 시키면 끝입니다. 이 때 이동평균선 및 이동표준편차는 일반적으로 20거래일을 기준으로 하고 두 지표간 거리는 2배수만큼 차이 나게 위치시키는 것이 일반적입니다.

> $(중심선; Center Line) = (종가 또는 Typical Price)의 20거래일 평균값$
$(상단선; Upper Line) = 중심선 + 2 x (종가 또는 Typical Price)의 20거래일 표준편차값$
$(하단선; Lower Line) = 중심선 - 2 x (종가 또는 Typical Price)의 20거래일 표준편차값$

이 때, Typical Price는 (종가 + 고가 + 저가) / 3으로 정의합니다.

## 개발 배경

In [ ]:
idex.period = 5
kospi = idex.kospi
kospi_bb = tools.bollinger_band(ohlcv=kospi, name='코스피')

fig = kospi_bb.figure_basic
fig['data'][3]['yhoverformat'] = ',d'
fig.update_layout(
    margin=dict(r=1),
    legend=dict(
        orientation="h",
        yanchor="bottom",
        y=1.02,
        xanchor="right",
        x=1
    )
)
fig.show()

볼린저 밴드는 직관적으로 지지/저항, 다시 말해 목표하는 매매 가격의 상한선과 하한선을 찾을 수 있도록 돕습니다.
경우에 따라서는 중심선이 지지/저항선의 역할을 할 수도 있죠.
그래서 이 지표의 개발 초기에는 하한선에 도달했을 때 매수, 상한선에 도달했을 때 매도하는 기법이 각광 받기도 했습니다.

## 한계점

물론 현재 이 방식으로 투자를 하는 것은 권하지 않는 위험한 방법입니다.
상승 또는 하락 추세에 있는 주식의 경우 지속적으로 상한선 또는 하한선을 타고 이동하며 변동성을 키우기도 하기 때문입니다.
무턱대고 주가가 밴드 하한선에 도달했다고 매수를 했다가는 큰 손실을 볼 수도 있습니다.
상기 사례에서 볼 수 있듯이 볼린저 밴드는 단독 사용 시 오인 신호(Fault Signal)을 만들 수 있습니다.
따라서 볼린저 밴드는 다른 지표들과 함께 보조 지표로 사용해야 하는 점을 꼭 유의해야합니다.

In [ ]:
skhynix = kr('000660')
skhynix.period = 5

skhynix_bb = tools.bollinger_band(ohlcv=skhynix.ohlcv, name='SK하이닉스', unit='KRW')
fig = skhynix_bb.figure_basic
fig['data'][3]['yhoverformat'] = ',d'
fig.update_layout(
    margin=dict(r=0),
    legend=dict(
        orientation="h",
        yanchor="bottom",
        y=1.02,
        xanchor="right",
        x=1
    )
)
fig.show()

## 변동성 지표: 밴드 폭

(밴드 폭; Width) = 

밴드의 폭은 이동표준편차, 즉 누적된 변동성을 나타냅니다. 밴드의 폭이 넓어진다는 말은 곧 주가의 변동성이 커진다는 말과 같습니다.
변동성은 다른 말로 리스크입니다. 높은 리스크에는 높은 수익률이 따라올 수도 있고, 처참한 수익률이 기다리고 있을 수도 있습니다.
따라서 변동성 지표를 활용한다면 적절한 리스크 관리를 할 수 있겠죠.

In [ ]:
kb = kr('105560')
kb.period = 5

kb_bb = tools.bollinger_band(ohlcv=kb.ohlcv, name='KB금융', unit='KRW')
fig = make_subplots(rows=3, cols=1, shared_xaxes=True, row_width=[0.3, 0.15, 0.55], vertical_spacing=0.01)

fig.add_trace(kb_bb.trace_upper_edge, row=1, col=1)

trace_middle = kb_bb.trace_middle
trace_middle.line = dict(color='rgb(197, 224, 180)')
fig.add_trace(trace_middle, row=1, col=1)

trace_lower = kb_bb.trace_lower_edge
trace_lower.line = dict(color='rgb(197, 224, 180)')
fig.add_trace(trace_lower, row=1, col=1)

trace_price = tools.draw_candle(data=kb.ohlcv, name='KB금융')
fig.add_trace(trace_price, row=1, col=1)

trace_volume = tools.draw_bar(data=kb.ohlcv.거래량, name="거래량")
trace_volume.marker = dict(color=kb.ohlcv.거래량.pct_change().apply(lambda x: 'blue' if x < 0 else 'red'))
fig.add_trace(trace_volume, row=2, col=1)

fig.add_trace(kb_bb.trace_width, row=3, col=1)

fig.update_layout(
    title=f"볼린저밴드와 변동성: {kb_bb.name}", plot_bgcolor="white", height=750,
    margin=dict(r=0),
    legend=dict(
        tracegroupgap=5,
        orientation="h",
        yanchor="bottom",
        y=1.02,
        xanchor="right",
        x=1
    ),
    xaxis=dict(
        showgrid=True, gridwidth=0.5, gridcolor='lightgrey', autorange=True,
        showline=True, linewidth=1, linecolor='grey', mirror=False
    ),
    yaxis=dict(
        title=f"{kb_bb.name}[{'-' if not kb_bb.curr else kb_bb.curr}]",
        showgrid=True, gridwidth=0.5, gridcolor='lightgrey', autorange=True,
        showline=True, linewidth=0.5, linecolor='grey', mirror=False
    ),
    xaxis2=dict(
        showgrid=True, gridwidth=0.5, gridcolor='lightgrey', autorange=True,
        showline=True, linewidth=1, linecolor='grey', mirror=False
    ),
    yaxis2=dict(
        title=f"거래량",
        showgrid=True, gridwidth=0.5, gridcolor='lightgrey', autorange=True,
        showline=True, linewidth=0.5, linecolor='grey', mirror=False
    ),
    xaxis3=dict(
        showticklabels=True, tickformat='%Y/%m/%d',
        showgrid=True, gridwidth=0.5, gridcolor='lightgrey', autorange=True,
        showline=True, linewidth=1, linecolor='grey', mirror=False
    ),
    yaxis3=dict(
        title=f"밴드 폭[%]",
        showgrid=True, gridwidth=0.5, gridcolor='lightgrey', autorange=True,
        showline=True, linewidth=0.5, linecolor='grey', mirror=False
    ),
    xaxis_rangeslider=dict(visible=False),
    xaxis_rangeselector=dict(
        buttons=list([
            dict(count=1, label="1m", step="month", stepmode="backward"),
            dict(count=3, label="3m", step="month", stepmode="backward"),
            dict(count=6, label="6m", step="month", stepmode="backward"),
            dict(count=1, label="YTD", step="year", stepmode="todate"),
            dict(count=1, label="1y", step="year", stepmode="backward"),
            dict(step="all")
        ])
    ),
)

## %B: 과매수/과매도 판단 지표


(밴드 대비 가격; %B) = 

일반적으로 가격이 상한성을 상회한다면 과매수(Over-Bought) 상태라고 합니다. 주가가 과열되었다는 것이죠. 이 경우는 확률적으로 주가가 하락할 가능성이 높다고 판단합니다.
반대로 가격이 하한선을 하회한다면 과매도(Over-Sold) 상태라고 합니다. 주가가 필요 이상으로 하락했다고 판단하며 주가의 상승 여력이 있는 가능성을 엿볼 수 있습니다.


이 외에도 볼린저 밴드를 활용한 다양한 투자 기법이 있습니다. 이어지는 칼럼에서 확인하세요!

In [ ]:
hyundai = kr('035420')
hyundai.period = 5

hyundai_bb = tools.bollinger_band(ohlcv=hyundai.ohlcv, name='NAVER', unit='KRW')

fig = make_subplots(rows=3, cols=1, shared_xaxes=True, row_width=[0.3, 0.15, 0.55], vertical_spacing=0.01)

fig.add_trace(hyundai_bb.trace_upper_edge, row=1, col=1)

trace_middle = hyundai_bb.trace_middle
trace_middle.line = dict(color='rgb(197, 224, 180)')
fig.add_trace(trace_middle, row=1, col=1)

trace_lower = hyundai_bb.trace_lower_edge
trace_lower.line = dict(color='rgb(197, 224, 180)')
fig.add_trace(trace_lower, row=1, col=1)

trace_price = tools.draw_candle(data=hyundai_bb.ohlcv, name=hyundai_bb.name)
fig.add_trace(trace_price, row=1, col=1)

trace_volume = tools.draw_bar(data=hyundai_bb.ohlcv.거래량, name="거래량")
trace_volume.marker = dict(color=hyundai_bb.ohlcv.거래량.pct_change().apply(lambda x: 'blue' if x < 0 else 'red'))
fig.add_trace(trace_volume, row=2, col=1)

fig.add_trace(hyundai_bb.trace_pctb, row=3, col=1)
fig.add_hrect(y0=1, y1=hyundai_bb.pctb.max(), line_width=0, fillcolor='red', opacity=0.2, row=3, col=1)
fig.add_hrect(y0=hyundai_bb.pctb.min(), y1=0, line_width=0, fillcolor='green', opacity=0.2, row=3, col=1)

fig.update_layout(
    title=f"볼린저밴드와 상대 매수 지표: {hyundai_bb.name}", plot_bgcolor="white", height=750,
    margin=dict(r=0),
    legend=dict(
        tracegroupgap=5,
        orientation="h",
        yanchor="bottom",
        y=1.02,
        xanchor="right",
        x=1
    ),
    xaxis=dict(
        showgrid=True, gridwidth=0.5, gridcolor='lightgrey', autorange=True,
        showline=True, linewidth=1, linecolor='grey', mirror=False
    ),
    yaxis=dict(
        title=f"{hyundai_bb.name}[{'-' if not hyundai_bb.curr else hyundai_bb.curr}]",
        showgrid=True, gridwidth=0.5, gridcolor='lightgrey', autorange=True,
        showline=True, linewidth=0.5, linecolor='grey', mirror=False
    ),
    xaxis2=dict(
        showgrid=True, gridwidth=0.5, gridcolor='lightgrey', autorange=True,
        showline=True, linewidth=1, linecolor='grey', mirror=False
    ),
    yaxis2=dict(
        title=f"거래량",
        showgrid=True, gridwidth=0.5, gridcolor='lightgrey', autorange=True,
        showline=True, linewidth=0.5, linecolor='grey', mirror=False
    ),
    xaxis3=dict(
        showticklabels=True, tickformat='%Y/%m/%d',
        showgrid=True, gridwidth=0.5, gridcolor='lightgrey', autorange=True,
        showline=True, linewidth=1, linecolor='grey', mirror=False
    ),
    yaxis3=dict(
        title=f"%B[-]",
        showgrid=True, gridwidth=0.5, gridcolor='lightgrey', autorange=True,
        showline=True, linewidth=0.5, linecolor='grey', mirror=False
    ),
    xaxis_rangeslider=dict(visible=False),
    xaxis_rangeselector=dict(
        buttons=list([
            dict(count=1, label="1m", step="month", stepmode="backward"),
            dict(count=3, label="3m", step="month", stepmode="backward"),
            dict(count=6, label="6m", step="month", stepmode="backward"),
            dict(count=1, label="YTD", step="year", stepmode="todate"),
            dict(count=1, label="1y", step="year", stepmode="backward"),
            dict(step="all")
        ])
    ),
)
fig.show()

재차 강조하지만 보조 지표는 투자를 돕는 분석 도구이지 선행 지표가 아닙니다. 이는 결코 완벽하지 않으며 여기에 대한 과한 의존성은 건강한 투자를 해치는 요인이 됩니다.
하지만 적절한 가설과 검증을 통해 만들어진 기법은 빠른 투자 의사결정에 도움이 될 수 있습니다.
[Snowballing]에서는 투자에 유익한 정보를 보다 안전하고 신뢰성있게 다루기 위해 노력하겠습니다. 

# Back-Test

In [3]:
basis = krse.wi26.join(krse.overview.drop(columns=['종목명']))
basis = basis.sort_values(by='시가총액', ascending=False)
basis

종목명      섹터        IPO      종가             시가총액       거래량  \
종목코드                                                                       
005930        삼성전자     반도체 1975-06-11   63900  381469104945000  13224089   
373220    LG에너지솔루션    IT가전 2022-01-27  517000  120744000000000    684338   
000660      SK하이닉스     반도체 1996-12-26   92300   66903417343500   2315420   
207940    삼성바이오로직스    건강관리 2016-11-10  795000   56583330000000     85041   
051910        LG화학      화학 2001-04-25  685000   48143977926000    256552   
...            ...     ...        ...     ...              ...       ...   
054220       비츠로시스   소프트웨어 2001-12-26     868      21740730912    271214   
064090     에프앤리퍼블릭  소매(유통) 2002-12-17    1515      20813125557    151771   
044180          KD      건설 2000-11-16     757      18785572596     26899   
161570  THE MIDONG     자동차 2013-11-13    1197      18777310150    124491   
174880        장원테크  IT하드웨어 2016-07-15     837      18335594025    112907   

                거래대금       상장주식수       BPS     PER    PBR      EPS   DIV  \
종목코드                                                                       
005930  842948312900  5969782550   43611.0   11.06   1.47   5777.0  2.26   
373220  345628576500   234000000   39831.0  130.46  12.98   3963.0  0.00   
000660  211753770000   728002365   90394.0    6.60   1.02  13989.0  1.67   
207940   67349833000    71174000   74551.0  135.23  10.66   5879.0  0.00   
051910  171719371000    70592343  278455.0   14.54   2.46  47108.0  1.75   
...              ...         ...       ...     ...    ...      ...   ...   
054220     231678836    25162883     559.0    3.98   1.55    218.0  0.00   
064090     231699115    13576729    1169.0   19.68   1.30     77.0  0.00   
044180      20475603    24848641    1578.0    0.00   0.48      0.0  0.00   
161570     151383615    15582830    1194.0    0.00   1.00      0.0  0.00   
174880      92695695    21906325    4845.0    0.00   0.17      0.0  0.00   

            DPS  
종목코드             
005930   1444.0  
373220      0.0  
000660   1540.0  
207940      0.0  
051910  12000.0  
...         ...  
054220      0.0  
064090      0.0  
044180      0.0  
161570      0.0  
174880      0.0  

[2257 rows x 14 columns]

## Stochastic Strategy

### Singular

In [4]:
fetch = kr('012330', basis)

stock = tools.bollinger_band(ohlcv=fetch.ohlcv, name=fetch.name, unit=fetch.curr)
est = tools.evaluate(stock.ohlcv, stock.obos_signal, fetch.name)
# est.edges
est.eval()

TRADING DAYS  BUY SIGNALED  OVER PERFORM  SUCCESS RATE  CUT LOSS RATE  \
현대모비스          4943           112            73         65.18          -5.15   

       AVERAGE RISE  AVERAGE DROP  BEST CASE BEST CASE DATE  WORST CASE  \
현대모비스          8.53         -6.86      43.75     2020-03-20      -42.47   

      WORST CASE DATE  
현대모비스      2020-02-26

In [5]:
fig = stock.figure_full
fig.update_layout(
    title=f"볼린저밴드 스토캐스틱 전략: {fetch.name}({fetch.ticker})", plot_bgcolor="white", height=750,
    margin=dict(r=0),
    legend=dict(
        tracegroupgap=5,
        orientation="h",
        yanchor="bottom",
        y=1.02,
        xanchor="right",
        x=1
    ),
)
fig.show()

### Plural :: Large Cap.

In [27]:
fetches = dict()
idex.kind

KOSPI                    KOSDAQ                      KRX  \
      지수                지수명     지수                지수명    지수   
0   1001                코스피   2001                코스닥  5042   
1   1002            코스피 대형주   2002            코스닥 대형주  5043   
2   1003            코스피 중형주   2003            코스닥 중형주  5044   
3   1004            코스피 소형주   2004            코스닥 소형주  5045   
4   1005               음식료품   2012              기타서비스  5046   
5   1006               섬유의복   2015             코스닥 IT  5048   
6   1007               종이목재   2024                제조업  5049   
7   1008                 화학   2026                 건설  5051   
8   1009                의약품   2027                 유통  5052   
9   1010              비금속광물   2029                 운송  5054   
10  1011               철강금속   2031                 금융  5055   
11  1012                 기계   2037              오락·문화  5056   
12  1013               전기전자   2041            통신방송서비스  5057   
13  1014               의료정밀   2042       IT S/W & SVC  5061   
14  1015               운수장비   2043             IT H/W  5062   
15  1016                유통업   2056             음식료·담배  5063   
16  1017              전기가스업   2058              섬유·의류  5064   
17  1018                건설업   2062              종이·목재  5065   
18  1019              운수창고업   2063            출판·매체복제  5300   
19  1020                통신업   2065                 화학  5351   
20  1021                금융업   2066                 제약  5352   
21  1022                      2067                비금속  5353   
22  1024                 증권   2068                 금속  5354   
23  1025                 보험   2070              기계·장비  5355   
24  1026               서비스업   2072             일반전기전자  5356   
25  1027                제조업   2074            의료·정밀기기  5357   
26  1028            코스피 200   2075            운송장비·부품  5358   
27  1034            코스피 100   2077               기타제조  5600   
28  1035             코스피 50   2151              통신서비스   NaN   
29  1150  코스피 200 커뮤니케이션서비스   2152              방송서비스   NaN   
30  1151         코스피 200 건설   2153                인터넷   NaN   
31  1152        코스피 200 중공업   2154             디지털컨텐츠   NaN   
32  1153      코스피 200 철강/소재   2155              소프트웨어   NaN   
33  1154     코스피 200 에너지/화학   2156             컴퓨터서비스   NaN   
34  1155       코스피 200 정보기술   2157               통신장비   NaN   
35  1156         코스피 200 금융   2158               정보기기   NaN   
36  1157      코스피 200 생활소비재   2159                반도체   NaN   
37  1158      코스피 200 경기소비재   2160               IT부품   NaN   
38  1159        코스피 200 산업재   2181          코스닥 우량기업부   NaN   
39  1160       코스피 200 헬스케어   2182          코스닥 벤처기업부   NaN   
40  1167       코스피 200 중소형주   2183          코스닥 중견기업부   NaN   
41  1182   코스피 200 초대형제외 지수   2184        코스닥 기술성장기업부   NaN   
42  1224   코스피 200 비중상한 30%   2189         코스닥 글로벌 지수   NaN   
43  1227   코스피 200 비중상한 25%   2203            코스닥 150   NaN   
44  1232   코스피 200 비중상한 20%   2212         코스닥 150 소재   NaN   
45  1244     코스피200제외 코스피지수   2213        코스닥 150 산업재   NaN   
46  1894     코스피 200 TOP 10   2214      코스닥 150 필수소비재   NaN   
47   NaN                NaN   2215      코스닥 150 자유소비재   NaN   
48   NaN                NaN   2216       코스닥 150 정보기술   NaN   
49   NaN                NaN   2217       코스닥 150 헬스케어   NaN   
50   NaN                NaN   2218  코스닥 150 커뮤니케이션서비스   NaN   

                         테마                                        
                  지수명    지수                                   지수명  
0             KRX 100  1163                            코스피 고배당 50  
1             KRX 자동차  1164                           코스피 배당성장 50  
2             KRX 반도체  1165                            코스피 우선주 지수  
3            KRX 헬스케어  1180                        코스피 200 ESG 지수  
4              KRX 은행  1185      KRX-IHS Markit 코스피 200 예측 고배당 50  
5           KRX 에너지화학  1186     KRX-IHS Markit 코스피 200 예측 배당성장 50  
6              KRX 철강  1187   KRX-IHS Markit 코스피 200 예측 고배당 50 TR  
7            KRX 방송통신  1188  KRX-IHS Markit 코스피 200

In [51]:
ests = list()

loop = tqdm(idex.deposit('5062'))
for ticker in loop:
    name = basis.loc[ticker, '종목명']
    loop.set_description(desc=f'{name}({ticker})')
    if not ticker in fetches.keys():
        f = kr(ticker)
        b = tools.bollinger_band(ohlcv=f.ohlcv, name=name, unit=f.curr)
        fetches[ticker] = tools.evaluate(b.ohlcv, b.obos_signal, name).eval()
    ests.append(fetches[ticker])

estimated = pd.concat(ests, axis=0)
estimated

  0%|          | 0/32 [00:00<?, ?it/s]

TRADING DAYS  BUY SIGNALED  OVER PERFORM  SUCCESS RATE  \
KT&G             4943            98            46         46.94   
LG생활건강           4943            94            63         67.02   
아모레퍼시픽           4097           101            61         60.40   
CJ제일제당           3789            82            47         57.32   
오리온              1366            26            16         61.54   
BGF리테일           1263            31            16         51.61   
아모레G             4943            96            61         63.54   
이마트              2867            77            34         44.16   
GS리테일            2731            68            40         58.82   
동원산업             4943            97            51         52.58   
농심               4943           105            50         47.62   
동서               4943           117            49         41.88   
오뚜기              4943           111            62         55.86   
하이트진로            3277           106            55         51.89   
롯데칠성             4943           133            68         51.13   
롯데제과             1292            28             7         25.00   
현대바이오            4943           101            78         77.23   
한국콜마             2527            63            33         52.38   
하림지주             1371            34            13         38.24   
오리온홀딩스           4943           101            63         62.38   
삼양식품             4943           106            72         67.92   
코스맥스             2166            50            31         62.00   
콜마비앤에이치          2094            48            27         56.25   
대상               4943           110            62         56.36   
현대그린푸드           4943           110            62         56.36   
SPC삼립            4943           106            75         70.75   
카나리아바이오          1147            30            23         76.67   
삼양홀딩스            4935           114            64         56.14   
풀무원              4943           120            70         58.33   
삼양사              2745            65            32         49.23   
매일유업             1389            41            12         29.27   
CJ프레시웨이          4943           111            61         54.95   

         CUT LOSS RATE  AVERAGE RISE  AVERAGE DROP  BEST CASE BEST CASE DATE  \
KT&G             -1.68          5.87         -4.07      23.87     2004-01-07   
LG생활건강           -5.29          8.75         -6.34      39.88     2017-09-26   
아모레퍼시픽           -5.74          8.56         -7.92      36.99     2007-10-09   
CJ제일제당           -4.04          7.52         -6.66      35.95     2011-07-05   
오리온              -6.76          8.52         -7.58      30.27     2018-11-02   
BGF리테일           -6.05          8.92         -7.68      37.50     2020-03-20   
아모레G             -8.48          9.07         -8.89      73.82     2008-10-29   
이마트              -4.61          6.02         -6.48      26.07     2011-08-10   
GS리테일            -4.47          7.07         -6.24      21.89     2012-01-26   
동원산업             -6.49         10.08         -6.83      60.13     2004-06-22   
농심               -3.78          6.58         -5.62      42.82     2008-10-30   
동서               -2.94          6.13         -4.97      43.55     2021-01-29   
오뚜기              -3.57          8.83         -6.50      65.84     2008-10-28   
하이트진로            -4.08          7.63         -5.93      35.35     2020-03-20   
롯데칠성             -5.10          7.58         -6.46      34.49     2008-10-28   
롯데제과             -3.29          5.27         -6.18      34.15     2020-03-24   
현대바이오           -16.98         19.58        -15.15     173.97     2019-03-12   
한국콜마             -7.01          9.47         -7.63      35.13     2020-03-16   
하림지주             -7.57          7.87         -8.73      68.94     2020-03-23   
오리온홀딩스           -5.06          8.69         -6.46      29.20     2020-03-24   
삼양식품             -8.40         16.87         -9.65     189.00     2008-06-13   
코스맥스            -10.00         10.16 

In [52]:
print(f"평균 성공률: {round(estimated['SUCCESS RATE'].mean(), 2)}%")
print(f"평균 누락 수익률: {round((estimated['AVERAGE RISE'] - 5).mean(), 2)}%")
print(f"평균 손절 수익률: {round(estimated['CUT LOSS RATE'].mean(), 2)}%")
print(f"평균 낙폭: {round(estimated['AVERAGE DROP'].mean(), 2)}%")

평균 성공률: 55.06%
평균 누락 수익률: 4.3%
평균 손절 수익률: -6.67%
평균 낙폭: -7.63%


In [10]:
estimated.to_csv(r'file.csv', encoding='euc-kr')